Introduction
This legacy project seeks to analyse the accessibility of Health facilities in areas in Ghana.

Datasets

Packages used

Results

In [1]:
#Iport all libraries

import os

from IPython.display import display

import folium
from folium.plugins import MarkerCluster

from openrouteservice import client

import time
import pandas as pd
import fiona as fn
from shapely.geometry import shape, mapping
from shapely.ops import cascaded_union
import numpy

# import zonal stats function from python file, get it here: https://gist.github.com/perrygeo/5667173
#from zonal_stats import *


In [2]:
#Use zonal statistics to determine population counts per district
import os
os.environ['USE_PYGEOS'] = '0'
import geopandas
from rasterstats import zonal_stats
import geopandas as gpd

districts_as_gdf = gpd.read_file("data_mentorship-20230223T152806Z-001/data_mentorship/mdg_adm_bngrc_ocha_20181031_shp/mdg_admbnda_adm3_BNGRC_OCHA_20181031.shp")
zonal_stats(districts_as_gdf, "data_mentorship-20230223T152806Z-001/data_mentorship/mdg_ppp_2020_1km_Aggregated_UNadj.tif",
            stats='count min mean max median')

[{'min': 6463.52734375,
  'max': 10556.763671875,
  'mean': 7820.617838541667,
  'count': 12,
  'median': 7901.0078125},
 {'min': 2255.928955078125,
  'max': 11751.80078125,
  'mean': 7125.559210526316,
  'count': 19,
  'median': 8297.447265625},
 {'min': 7548.60546875,
  'max': 10122.046875,
  'mean': 8673.1203125,
  'count': 10,
  'median': 8726.50390625},
 {'min': 1462.2344970703125,
  'max': 8493.7841796875,
  'mean': 6022.139705882353,
  'count': 17,
  'median': 7044.3310546875},
 {'min': 2476.57763671875,
  'max': 27318.796875,
  'mean': 14647.202546296296,
  'count': 27,
  'median': 13785.6640625},
 {'min': 3871.896240234375,
  'max': 27921.82421875,
  'mean': 12738.134868421053,
  'count': 19,
  'median': 10824.9375},
 {'min': 495.50396728515625,
  'max': 10726.5322265625,
  'mean': 2427.25375,
  'count': 25,
  'median': 1435.4896240234375},
 {'min': 1010.8953857421875,
  'max': 25519.927734375,
  'mean': 9862.172619047618,
  'count': 42,
  'median': 8832.708984375},
 {'min': 2

In [ ]:
#Export zonal statistics as csv


In [3]:
# insert your ORS api key
api_key = '5b3ce3597851110001cf6248b1ddbe33f9af42859cde1756ab2fefff'
ors = client.Client(key=api_key)

# make sure to provide the right filenames
districts_filename = 'data_mentorship-20230223T152806Z-001/data_mentorship/mdg_adm_bngrc_ocha_20181031_shp/mdg_admbnda_adm3_BNGRC_OCHA_20181031.shp'
health_facilities_filename = 'data_mentorship-20230223T152806Z-001/data_mentorship/madagascar-shapefiles/shapefiles/healthsites.shp'
population_raster_filename = 'data_mentorship-20230223T152806Z-001/data_mentorship/mdg_ppp_2020_1km_Aggregated_UNadj.tif'

# these files will be generated during processing
isochrones_car_filename = 'data_mentorship-20230223T152806Z-001/data_mentorship/iso_union_car.shp'
isochrones_car_per_district_filename = 'data_mentorship-20230223T152806Z-001/data_mentorship/iso_car_per_district.shp'
isochrones_foot_filename = 'data_mentorship-20230223T152806Z-001/data_mentorship/iso_union_foot.shp'
isochrones_foot_per_district_filename = 'data_mentorship-20230223T152806Z-001/data_mentorship/iso_foot_per_district.shp'

# final file with all generated information
output_file = 'data_mentorship-20230223T152806Z-001/data_mentorship/districts_final.geojson'

In [4]:
#Convert health facility shapefile to dictionary

districts_dictionary = {}
with fn.open(districts_filename, 'r') as districts:
    for feature in districts:
        district_id = int(feature['id'])
        districts_dictionary[district_id] = {
            'District Code': feature['properties']['ADM3_PCODE'],
            'District Name': feature['properties']['ADM3_EN'],
            'Population Count': 0,
            'Car: Pop. with access': 0,
            'Car: Pop. with access [%]': 0.0,
            'Foot: Pop. with access': 0,
            'Foot: Pop. with access [%]': 0.0,
            'geometry': feature['geometry']
        }
print('created dictionary for %s districts' % len(districts_dictionary))

facilities_dictionary = {}
with fn.open(health_facilities_filename, 'r') as facilities:
    for feature in facilities:
        facility_id = int(feature['id'])
        facilities_dictionary[facility_id] = {
            'geometry': feature['geometry']
        }
print('created dictionary for %s facilities' % len(facilities_dictionary))

created dictionary for 1579 districts
created dictionary for 545 facilities


In [8]:
map_outline = folium.Map(location=[-18.812718, 46.713867], zoom_start=5)
folium.TileLayer('Stamen Toner').add_to(map_outline)


# Import health facilities
cluster = MarkerCluster().add_to(map_outline)  # To cluster hospitals

for facility_id in facilities_dictionary:
    folium.Marker(list(reversed(facilities_dictionary[facility_id]['geometry']['coordinates']))).add_to(cluster)

# Import district boundaries
district_simp = []
for district_id in districts_dictionary:
    geom = shape(districts_dictionary[district_id]['geometry'])
    # we simplify the geometry just for the purpose of visualisation
    # be aware that some browsers e.g. chrome might fail to render the entire map if there are to many coordinates
    simp_geom = geom.simplify(0.005, preserve_topology=False)
    simp_coord = mapping(simp_geom)
    folium.GeoJson(simp_coord).add_to(map_outline)
    district_simp.append(simp_coord)
    
#add layer control to switch between types of basemap tiles
folium.LayerControl().add_to(map_outline)

map_outline.save(os.path.join('data_mentorship-20230223T152806Z-001/data_mentorship', '1_health_facilities_overview.html'))
map_outline

In [5]:
from pprint import pprint
iso_params = {'locations': [[47.678548, -18.334123]],
                      'profile': 'driving-car',
                      'range_type': 'time',
                      'range': [3600]}
                
try:
    request = ors.isochrones(**iso_params)
    pprint(request)
except Exception as err:
    pprint(err)

{'bbox': [47.5417, -18.509969, 47.852227, -18.198975],
 'features': [{'geometry': {'coordinates': [[[47.5417, -18.393824],
                                             [47.544824, -18.398295],
                                             [47.551201, -18.401729],
                                             [47.553923, -18.408666],
                                             [47.554037, -18.409156],
                                             [47.554178, -18.409362],
                                             [47.55767, -18.408485],
                                             [47.558345, -18.40524],
                                             [47.559082, -18.402556],
                                             [47.568805, -18.395817],
                                             [47.571252, -18.394916],
                                             [47.573732, -18.393642],
                                             [47.581949, -18.401213],
                                       

In [6]:
#we are using the facilities coordinates to calculate isochrones
# the facilities are stored in a dictionary
print("There are {} facilities".format(len(facilities_dictionary.keys())))
#545 facilities take a long time to run through the openroute api, as such we create a subset, 
#here we only keep 3 facilities to test
included_keys = [0,1,2,3,4,5,6,7,8,9]
t = {k:v for k,v in facilities_dictionary.items() if k in included_keys}
t

There are 545 facilities


{0: {'geometry': {'type': 'Point',
   'coordinates': (49.29237954133279, -12.271964678135532)}},
 1: {'geometry': {'type': 'Point',
   'coordinates': (47.599301484956044, -21.39445040363148)}},
 2: {'geometry': {'type': 'Point',
   'coordinates': (47.55533387658326, -18.838001703122643)}},
 3: {'geometry': {'type': 'Point',
   'coordinates': (47.55940505077368, -18.87844036262132)}},
 4: {'geometry': {'type': 'Point',
   'coordinates': (47.55526045111145, -18.834916911297682)}},
 5: {'geometry': {'type': 'Point',
   'coordinates': (48.18033677314372, -21.097415620272642)}},
 6: {'geometry': {'type': 'Point',
   'coordinates': (47.085702463474746, -21.450277902080614)}},
 7: {'geometry': {'type': 'Point',
   'coordinates': (47.478816236883546, -18.85215982723011)}},
 8: {'geometry': {'type': 'Point',
   'coordinates': (47.68832173906745, -21.67375553394058)}},
 9: {'geometry': {'type': 'Point',
   'coordinates': (47.603236620857956, -22.722178902671402)}}}

In [18]:
"""
calculate the isochrones using the openroute api
"""
request_counter = 0
iso_car = [] # this is a list used to store our results
for facility_id in t.keys():
    try:
        loc = t[facility_id] #access our facility subset and get the coordinates
        # request isochrones from ORS api for car
        iso_params = {'locations': [list(loc['geometry']['coordinates'])],
                      'profile': 'driving-car',
                      'range_type': 'time',
                      'range': [3600]  # 3600 = 1hour
                     }
        request = ors.isochrones(**iso_params) # the actual calculation of isochrones
        request_counter += 1
        lon, lat = loc['geometry']['coordinates']
        iso_car.append(shape(request['features'][0]['geometry'])) #convert the output of the isochrones to a shapely geometry
        if len(iso_car) % 39 == 0:
            time.sleep(60)
    except Exception as err:
        pass
print('requested %s isochrones for car from ORS API' % request_counter)

requested 9 isochrones for car from ORS API


In [21]:
#write the isochrones to a shapefile
isochrones_car_filename = 'Mentorship_legacy/data_mentorship-20230223T152806Z-001/data_mentorship/output/iso_union_car.shp' #specify the folder where to store your output

# generate cascaded union of all isochrones
iso_union_car = cascaded_union(iso_car)
print('computed cascaded union of all isochrones')

# save isochrones to shapefiles, define a schema
schema = {'geometry': 'Polygon',
          'properties': {'id': 'int'}}
index = 0
with fn.open(isochrones_car_filename, 'w', 'ESRI Shapefile', schema) as c:
    for poly in iso_car:
        index += 1
        c.write({'geometry': mapping(poly),
                 'properties': {'id': index}})
        
print('saved isochrones as shapefiles for car')

C:\Users\prisc\AppData\Local\Temp\ipykernel_16992\3278874454.py:5: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  iso_union_car = cascaded_union(iso_car)


computed cascaded union of all isochrones
Unexpected exception formatting exception. Falling back to standard exception


Traceback (most recent call last):
  File "fiona\ogrext.pyx", line 1133, in fiona.ogrext.WritingSession.start
  File "fiona\_err.pyx", line 291, in fiona._err.exc_wrap_pointer
fiona._err.CPLE_AppDefinedError: Failed to create file Mentorship_legacy/data_mentorship-20230223T152806Z-001/data_mentorship/output\iso_union_car.shp: No such file or directory

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "C:\Users\prisc\.conda\envs\Mentorship\lib\site-packages\IPython\core\interactiveshell.py", line 3460, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "C:\Users\prisc\AppData\Local\Temp\ipykernel_16992\3278874454.py", line 12, in <module>
    with fn.open(isochrones_car_filename, 'w', 'ESRI Shapefile', schema) as c:
  File "C:\Users\prisc\.conda\envs\Mentorship\lib\site-packages\fiona\env.py", line 417, in wrapper
    return f(*args, **kwargs)
  File "C:\Users\prisc\.conda\envs\Mentorship\lib\site-packag

In [22]:
# Create isochrones with one-hour car driving range of one coordinate (HF)
map_isochrones = folium.Map(tiles='Stamen Terrain', location=([-18.812718, 46.713867]),
                            zoom_start=5)  # New map for isochrones

union_coord_car = mapping(iso_union_car)
folium.GeoJson(union_coord_car).add_to(map_isochrones)
map_isochrones

In [28]:
#For footwalking

from pprint import pprint
iso_params = {'locations': [[47.678548, -18.334123]],
                      'profile': 'foot-walking',
                      'range_type': 'time',
                      'range': [600]}
                
try:
    request = ors.isochrones(**iso_params)
    pprint(request)
except Exception as err:
    pprint(err)
    
"""
calculate the isochrones using the openroute api
"""
request_counter = 0
iso_foot = [] # this is a list used to store our results
for facility_id in t.keys():
    try:
        loc = t[facility_id] #access our facility subset and get the coordinates
        # request isochrones from ORS api for car
        iso_params = {'locations': [list(loc['geometry']['coordinates'])],
                      'profile': 'foot-walking',
                      'range_type': 'time',
                      'range': [600]  # 600 = 10minutes
                     }
        request = ors.isochrones(**iso_params) # the actual calculation of isochrones
        request_counter += 1
        lon, lat = loc['geometry']['coordinates']
        iso_car.append(shape(request['features'][0]['geometry'])) #convert the output of the isochrones to a shapely geometry
        if len(iso_foot) % 39 == 0:
            time.sleep(60)
    except Exception as err:
        pass
print('requested %s isochrones for car from ORS API' % request_counter)


{'bbox': [47.671496, -18.340618, 47.684667, -18.327556],
 'features': [{'geometry': {'coordinates': [[[47.671496, -18.331237],
                                             [47.671766, -18.331257],
                                             [47.672036, -18.331276],
                                             [47.672241, -18.331261],
                                             [47.67254, -18.331202],
                                             [47.676175, -18.33589],
                                             [47.675801, -18.336504],
                                             [47.675564, -18.336844],
                                             [47.675413, -18.337095],
                                             [47.675094, -18.33761],
                                             [47.674636, -18.338287],
                                             [47.674466, -18.338569],
                                             [47.674443, -18.338756],
                                    

In [30]:
#write the isochrones to a shapefile
isochrones_foot_filename = 'data_mentorship-20230223T152806Z-001/data_mentorship/iso_union_foot.shp' #specify the folder where to store your output

# generate cascaded union of all isochrones
iso_union_foot = cascaded_union(iso_foot)
print('computed cascaded union of all isochrones')

# Create isochrones with one-hour car driving range of one coordinate (HF)
map_isochrones = folium.Map(tiles='Stamen Terrain', location=([-18.812718, 46.713867]),
                            zoom_start=5)  # New map for isochrones
union_coord_car = mapping(iso_union_car)
folium.GeoJson(union_coord_car).add_to(map_isochrones)
union_coord_foot = mapping(iso_union_foot)
folium.GeoJson(union_coord_foot).add_to(map_isochrones)

union_coord_car.plot(ax=ax, color="#F0EAD7", edgecolor = "#828282", linewidth =0.25)
union_coord_foot.plot(ax=ax, color="red", edgecolor = "#828282", linewidth =0.25)

map_isochrones


computed cascaded union of all isochrones


C:\Users\prisc\AppData\Local\Temp\ipykernel_16992\2856922742.py:5: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  iso_union_foot = cascaded_union(iso_foot)
